## Import 套件

In [2]:
# import the neural net stuff
from keras.models import Sequential
from keras import optimizers
from keras.layers.core import Dense, Dropout, Activation, Flatten
from keras.layers.convolutional import Convolution1D
from keras.layers.normalization import BatchNormalization
from keras.layers.advanced_activations import LeakyReLU
from keras.regularizers import l2
from keras.models import model_from_json

# import other stuff
import random
import math
import numpy as np

Using TensorFlow backend.


## 宣告訓練物件

In [3]:
class Agent:
    def __init__(self, network=None, fitness=None):
        self.network = network
        self.fitness = fitness
        self.nr_simulations = 0

    def setNetwork(self, network):
        self.network = network

    def setFitness(self, fitness):
        self.fitness = fitness

    def setNrSimulations(self, nr_simulations):
        self.nr_simulations = nr_simulations

    def __repr__(self):
        return 'Agent {0}'.format(self.fitness)
class ScoreCounter:
    def __init__(self):
        self.last100 = []
        self.i = 0

    def add(self, new):
        if len(self.last100) < 100:
            self.last100.append(new)
        else:
            if self.i == 100:
                self.i = 0
            self.last100[self.i] = new
            self.i += 1

    def average(self):
        return sum(self.last100)/len(self.last100)


class Connection:
    def __init__(self, i, j, k):
        self.i = i
        self.j = j
        self.k = k

## 宣告SA優化物件

In [4]:
class SA:
    def __init__(self, inputs, outputs, nr_rounds_per_epoch, env, steps, epochs, scoreTarget = 1e9, starting_temp = 300, final_temp = 0.1, max_change = 1.0):
        self.input_size = inputs
        self.output_size = outputs
        self.nr_rounds_per_epoch = nr_rounds_per_epoch # 跑幾輪
        self.env = env
        self.steps = steps
        self.epochs = epochs # 幾個迭代
        self.scoreTarget = scoreTarget
        self.starting_temp = starting_temp # 初始溫度
        self.temp = starting_temp
        self.final_temp = final_temp # 最終溫度
        self.max_change = max_change
        self.score_counter = ScoreCounter()
   
    def initAgent(self, hiddenLayers):
        self.hiddenLayers = hiddenLayers
        agent = Agent()

        model = self.createModel(self.input_size, self.output_size, hiddenLayers, "relu")
        agent.setNetwork(model)
#         print(agent)
        self.agent = agent

    def cloneAgent(self, agent):
        newAgent = Agent()
        newNetwork = self.createModel(self.input_size, self.output_size, self.hiddenLayers, "relu")
        newNetwork.set_weights(agent.network.get_weights())
        newAgent.setNetwork(newNetwork)
        return newAgent

    def createRegularizedModel(self, inputs, outputs, hiddenLayers, activationType):
        bias = False
        dropout = 0.1
        regularizationFactor = 0
        model = Sequential()
        if len(hiddenLayers) == 0: 
            model.add(Dense(self.output_size, input_shape=(self.input_size,), init='lecun_uniform', bias=bias))
            model.add(Activation("linear"))
        else :
            if regularizationFactor > 0:
                model.add(Dense(hiddenLayers[0], input_shape=(self.input_size,), init='lecun_uniform', W_regularizer=l2(regularizationFactor),  bias=bias))
            else:
                model.add(Dense(hiddenLayers[0], input_shape=(self.input_size,), init='lecun_uniform', bias=bias))

            if (activationType == "LeakyReLU") :
                model.add(LeakyReLU(alpha=0.01))
            else :
                model.add(Activation(activationType))
            
            for index in range(1, len(hiddenLayers)-1):
                layerSize = hiddenLayers[index]
                if regularizationFactor > 0:
                    model.add(Dense(layerSize, init='lecun_uniform', W_regularizer=l2(regularizationFactor), bias=bias))
                else:
                    model.add(Dense(layerSize, init='lecun_uniform', bias=bias))
                if (activationType == "LeakyReLU") :
                    model.add(LeakyReLU(alpha=0.01))
                else :
                    model.add(Activation(activationType))
                if dropout > 0:
                    model.add(Dropout(dropout))
            model.add(Dense(self.output_size, init='lecun_uniform', bias=bias))
            model.add(Activation("linear"))
        optimizer = optimizers.RMSprop(lr=learningRate, rho=0.9, epsilon=1e-06)
        model.compile(loss="mse", optimizer=optimizer)
        return model

    def createModel(self, inputs, outputs, hiddenLayers, activationType):
        model = Sequential()
        if len(hiddenLayers) == 0: 
            model.add(Dense(self.output_size, input_shape=(self.input_size,), init='lecun_uniform'))
            model.add(Activation("linear"))
        else :
            model.add(Dense(hiddenLayers[0], input_shape=(self.input_size,), init='lecun_uniform'))
            if (activationType == "LeakyReLU") :
                model.add(LeakyReLU(alpha=0.01))
            else :
                model.add(Activation(activationType))
            
            for index in range(1, len(hiddenLayers)-1):
                layerSize = hiddenLayers[index]
                model.add(Dense(layerSize, init='lecun_uniform'))
                if (activationType == "LeakyReLU") :
                    model.add(LeakyReLU(alpha=0.01))
                else :
                    model.add(Activation(activationType))
            model.add(Dense(self.output_size, init='lecun_uniform'))
            model.add(Activation("linear"))
        optimizer = optimizers.RMSprop(lr=1, rho=0.9, epsilon=1e-06)
        model.compile(loss="mse", optimizer=optimizer)
        return model

    def backupNetwork(self, model, backup):
        weights = model.get_weights()
        backup.set_weights(weights)

    # predict Q values for all the actions
    def getValues(self, state, agent):
#         print(agent)
#         print(state)
        predicted = agent.network.predict(state.reshape(1,len(state)))
        return predicted[0]

    def getMaxValue(self, values):
        return np.max(values)

    def getMaxIndex(self, values):
        return np.argmax(values)

    # select the action with the highest value
    def selectAction(self, qValues):
        action = self.getMaxIndex(qValues)
        return action

    # could be useful in stochastic environments
    def selectActionByProbability(self, qValues, bias):
        qValueSum = 0
        shiftBy = 0
        for value in qValues:
            if value + shiftBy < 0:
                shiftBy = - (value + shiftBy)
        shiftBy += 1e-06

        for value in qValues:
            qValueSum += (value + shiftBy) ** bias

        probabilitySum = 0
        qValueProbabilities = []
        for value in qValues:
            probability = ((value + shiftBy) ** bias) / float(qValueSum)
            qValueProbabilities.append(probability + probabilitySum)
            probabilitySum += probability
        qValueProbabilities[len(qValueProbabilities) - 1] = 1

        rand = random.random()
        i = 0
        for value in qValueProbabilities:
            if (rand <= value):
                return i
            i += 1

    def run_simulation(self, env, agent, steps, render = False):
        observation = env.reset()
        totalReward = 0
        for t in range(steps):
            if (render):
                env.render()
            values = self.getValues(observation, agent)
            action = self.selectAction(values)
            newObservation, reward, done, info = env.step(action)
            totalReward += reward
            observation = newObservation
            if done:
                break
        if (agent.nr_simulations == 0):
            agent.setFitness(totalReward)
            agent.setNrSimulations(1)
        else :
            old_fitness = agent.fitness
            nr_simulations = agent.nr_simulations
            new_fitness = (old_fitness * nr_simulations + totalReward) / (nr_simulations + 1)
            agent.setNrSimulations(nr_simulations + 1)
            agent.setFitness(new_fitness)
        self.score_counter.add(totalReward)
        return totalReward

    def createWeightLayerList(self):
        weightLayerList = []
        for i in range(len(self.hiddenLayers)):
            weightLayerList.append(i * 2)
        return weightLayerList

    def mutate(self, agent, mutationFactor):
        new_weights = agent.network.get_weights()
        i = random.sample(self.createWeightLayerList(),1)[0]
        layer = new_weights[i]
        j = random.sample(range(len(layer)),1)[0]
        neuronConnectionGroup = layer[j]
        k = random.sample(range(len(neuronConnectionGroup)), 1)[0]
        rand = (random.random() - 0.5) * mutationFactor
        new_weights[i][j][k] = neuronConnectionGroup[k] + rand
        agent.network.set_weights(new_weights)

    def tryAgent(self, agent, nr_episodes):
        total = 0
        for i in range(nr_episodes):
            total += self.run_simulation(self.env, agent, self.steps)
        return total / nr_episodes

    def decrease_temp(self):
        amount_decrease = (self.starting_temp - self.final_temp) / self.epochs
        self.temp -= amount_decrease

    def sa(self):
        self.tryAgent(self.agent, 100)
        for e in range(self.epochs):
            newAgent = self.cloneAgent(self.agent)
            self.mutate(newAgent, self.max_change)
            self.tryAgent(newAgent, self.nr_rounds_per_epoch)

            if (self.agent.fitness < newAgent.fitness):
                self.agent = newAgent
            else :
                rand = random.random()
                probability = math.exp((newAgent.fitness - self.agent.fitness)/ self.temp)
#                 print (probability)
                if rand < probability:
                    self.agent = newAgent

            average = self.score_counter.average()
            print ("Epoch:",e," fitness:",self.agent.fitness," average: ",average)

            if average >= self.scoreTarget:
                break

            self.decrease_temp()



In [6]:
# import the gym stuff
import gym
# import other stuff
import random
import numpy as np
# import own classes
from simulated_annealing import SA

env = gym.make('CartPole-v0')

<TimeLimit<CartPoleEnv<CartPole-v0>>>

In [2]:
# import the gym stuff
import gym
# import other stuff
import random
import numpy as np
# import own classes
from simulated_annealing import SA

env = gym.make('CartPole-v0')

# 設定參數
epochs = 1000
steps = 200
scoreTarget = 200
starting_temp = 1
final_temp = 0.001

sa = SA(len(env.observation_space.high), env.action_space.n, 10, env, steps, epochs, scoreTarget = scoreTarget, starting_temp = starting_temp, final_temp = final_temp, max_change= 1.0)

# network size for the agents
sa.initAgent([4])

sa.sa()

C:\Users\rockm\OneDrive\桌面\Rock文件\meta heuristic nn\template\simulated_annealing.py:136: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(4, input_shape=(4,), kernel_initializer="lecun_uniform")`
  model.add(Dense(hiddenLayers[0], input_shape=(self.input_size,), init='lecun_uniform'))
C:\Users\rockm\OneDrive\桌面\Rock文件\meta heuristic nn\template\simulated_annealing.py:149: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(2, kernel_initializer="lecun_uniform")`
  model.add(Dense(self.output_size, init='lecun_uniform'))


Agent None
Agent None
[ 0.02875226 -0.00942874  0.02136823 -0.03416034]
Agent None
[ 0.02856368  0.18538037  0.02068502 -0.32002551]
Agent None
[ 0.03227129 -0.01002996  0.01428451 -0.02089175]
Agent None
[ 0.03207069  0.18488425  0.01386668 -0.30903374]
Agent None
[ 0.03576838 -0.0104325   0.007686   -0.0120101 ]
Agent None
[ 0.03555973  0.18457838  0.0074458  -0.30225812]
Agent None
[ 0.03925129 -0.01064889  0.00140064 -0.00723628]
Agent None
[ 0.03903832  0.18445294  0.00125591 -0.29947696]
Agent None
[ 0.04272737 -0.01068689 -0.00473362 -0.00639821]
Agent None
[ 0.04251364  0.18450263 -0.00486159 -0.30057088]
Agent None
[ 0.04620369 -0.01054969 -0.01087301 -0.00942516]
Agent None
[ 0.0459927   0.18472649 -0.01106151 -0.30551872]
Agent None
[ 0.04968723 -0.0102361  -0.01717188 -0.01634475]
Agent None
[ 0.0494825   0.18512786 -0.01749878 -0.31439576]
Agent None
[ 0.05318506 -0.00974051 -0.02378669 -0.02728234]
Agent None
[ 0.05299025  0.18571434 -0.02433234 -0.32737431]
Agent None
[ 

[ 0.0349964   0.19699182 -0.00271924 -0.28815646]
Agent 23.444444444444443
[ 0.03893624  0.00190876 -0.00848237  0.0036676 ]
Agent 23.444444444444443
[ 0.03897441  0.19715132 -0.00840902 -0.2916795 ]
Agent 23.444444444444443
[ 0.04291744  0.00215027 -0.01424261 -0.00166049]
Agent 23.444444444444443
[ 0.04296044  0.19747356 -0.01427582 -0.29880289]
Agent 23.444444444444443
[ 0.04690991  0.00255798 -0.02025188 -0.01065626]
Agent 23.444444444444443
[ 0.04696107  0.19796443 -0.020465   -0.30965947]
Agent 23.444444444444443
[ 0.05092036  0.00313995 -0.02665819 -0.02350024]
Agent 23.444444444444443
[ 0.05098316  0.19863386 -0.0271282  -0.32447349]
Agent 23.444444444444443
[ 0.05495584  0.00390847 -0.03361767 -0.0404676 ]
Agent 23.444444444444443
[ 0.05503401  0.19949596 -0.03442702 -0.3435648 ]
Agent 23.444444444444443
[ 0.05902393  0.00488026 -0.04129832 -0.06193378]
Agent 23.444444444444443
[ 0.05912153  0.20056926 -0.04253699 -0.36735524]
Agent 23.444444444444443
[ 0.06313292  0.00607675 

[ 0.05226649  0.22108921 -0.00624898 -0.25881849]
Agent 19.52173913043478
[ 0.05668827  0.02605703 -0.01142535  0.03188689]
Agent 19.52173913043478
[ 0.05720941  0.22134094 -0.01078762 -0.26437885]
Agent 19.52173913043478
[ 0.06163623  0.02637461 -0.01607519  0.02488213]
Agent 19.52173913043478
[ 0.06216372  0.22172336 -0.01557755 -0.27282904]
Agent 19.52173913043478
[ 0.06659819  0.02682711 -0.02103413  0.01490026]
Agent 19.52173913043478
[ 0.06713473  0.2222443  -0.02073613 -0.28434427]
Agent 19.52173913043478
[ 0.07157962  0.02742415 -0.02642301  0.00172716]
Agent 19.52173913043478
[ 0.0721281   0.22291488 -0.02638847 -0.29917405]
Agent 19.52173913043478
[ 0.0765864   0.02817882 -0.03237195 -0.01492896]
Agent 19.52173913043478
[ 0.07714998  0.22374971 -0.03267053 -0.31764729]
Agent 19.52173913043478
[ 0.08162497  0.02910795 -0.03902347 -0.03544388]
Agent 19.52173913043478
[ 0.08220713  0.22476715 -0.03973235 -0.34017923]
Agent 19.52173913043478
[ 0.08670247  0.03023239 -0.04653594 -

Agent 18.194444444444443
[ 0.05341677 -0.04392232 -0.06626825 -0.13081634]
Agent 18.194444444444443
[ 0.05253833  0.15208324 -0.06888458 -0.44364796]
Agent 18.194444444444443
[ 0.05557999 -0.04199986 -0.07775754 -0.17344979]
Agent 18.194444444444443
[ 0.05473999  0.15414387 -0.08122654 -0.48961408]
Agent 18.194444444444443
[ 0.05782287 -0.03974387 -0.09101882 -0.22359571]
Agent 18.194444444444443
[ 0.05702799  0.15655313 -0.09549073 -0.543545  ]
Agent 18.194444444444443
[ 0.06015906 -0.03710631 -0.10636163 -0.28241086]
Agent 18.194444444444443
[ 0.05941693 -0.23056309 -0.11200985 -0.02507694]
Agent 18.194444444444443
[ 0.05480567 -0.42391537 -0.11251139  0.23027192]
Agent 18.194444444444443
[ 0.04632736 -0.61726479 -0.10790595  0.48545371]
Agent 18.194444444444443
[ 0.03398207 -0.81071179 -0.09819688  0.74227369]
Agent 18.194444444444443
[ 0.01776783 -1.004351   -0.0833514   1.00250974]
Agent 18.194444444444443
[-0.00231919 -1.19826639 -0.06330121  1.26789604]
Agent 18.194444444444443


...

[ 0.04019397  0.01820912 -0.06279777 -0.29480361]
Agent 61.5
[ 0.04055815 -0.17596395 -0.06869384 -0.02256853]
Agent 61.5
[ 0.03703887  0.02007246 -0.06914521 -0.33610973]
Agent 61.5
[ 0.03744032 -0.17400083 -0.0758674  -0.06600791]
Agent 61.5
[ 0.03396031  0.02212224 -0.07718756 -0.3816299 ]
Agent 61.5
[ 0.03440275 -0.1718237  -0.08482016 -0.11424782]
Agent 61.5
[ 0.03096628  0.02440474 -0.08710512 -0.43243953]
Agent 61.5
[ 0.03145437 -0.16938286 -0.09575391 -0.16843671]
Agent 61.5
[ 0.02806672 -0.36301308 -0.09912264  0.09256947]
Agent 61.5
[ 0.02080645 -0.16662042 -0.09727125 -0.22966786]
Agent 61.5
[ 0.01747405 -0.36022752 -0.10186461  0.03081732]
Agent 61.5
[ 0.0102695  -0.16380348 -0.10124826 -0.29218786]
Agent 61.5
[ 0.00699343 -0.35734703 -0.10709202 -0.03307547]
Agent 61.5
[-1.53514649e-04 -1.60865301e-01 -1.07753531e-01 -3.57534540e-01]
Agent 61.5
[-0.00337082 -0.35430355 -0.11490422 -0.10067829]
Agent 61.5
[-0.01045689 -0.54760728 -0.11691779  0.15365772]
Agent 61.5
[-0.0214

Agent 65.2
[-0.43800411 -1.53495845 -0.07835631  0.63079393]
Agent 65.2
[-0.46870327 -1.33883566 -0.06574044  0.3144992 ]
Agent 65.2
[-0.49547999 -1.53296255 -0.05945045  0.58574676]
Agent 65.2
[-0.52613924 -1.72720362 -0.04773552  0.85912549]
Agent 65.2
[-0.56068331 -1.53146508 -0.03055301  0.55182323]
Agent 65.2
[-0.59131261 -1.72614492 -0.01951654  0.8347255 ]
Agent 65.2
[-0.62583551 -1.92099488 -0.00282203  1.12120728]
Agent 65.2
[-0.66425541 -1.72583603  0.01960211  0.8276405 ]
Agent 65.2
[-0.69877213 -1.92122044  0.03615492  1.12642346]
Agent 65.2
[-0.73719654 -2.11679701  0.05868339  1.43022383]
Agent 65.2
[-0.77953248 -1.92244661  0.08728787  1.15644307]
Agent 65.2
[-0.81798141 -2.11859123  0.11041673  1.47516992]
Agent 65.2
[-0.86035324 -1.92497805  0.13992013  1.21891533]
Agent 65.2
[-0.8988528  -2.12159859  0.16429844  1.55196625]
Agent 65.2
[-0.94128477 -2.31826534  0.19533776  1.89108042]
Agent 70.5
[-0.01817743  0.04401692  0.02975182  0.0430451 ]
Agent 70.5
[-0.01729709 

Agent 60.22222222222222
[-0.06472965  0.00173547  0.09040914  0.23022911]
Agent 60.22222222222222
[-0.06469494 -0.19455428  0.09501372  0.55000532]
Agent 60.22222222222222
[-0.06858603 -0.00088632  0.10601383  0.28870569]
Agent 60.22222222222222
[-0.06860376  0.1925767   0.11178794  0.03125008]
Agent 60.22222222222222
[-0.06475222 -0.00395606  0.11241294  0.3570064 ]
Agent 60.22222222222222
[-0.06483134  0.18940318  0.11955307  0.10177801]
Agent 60.22222222222222
[-0.06104328 -0.00721119  0.12158863  0.42965937]
Agent 60.22222222222222
[-0.0611875   0.18599801  0.13018182  0.17764425]
Agent 60.22222222222222
[-0.05746754 -0.01072336  0.13373471  0.50839484]
Agent 60.22222222222222
[-0.05768201  0.18228597  0.1439026   0.26066688]
Agent 60.22222222222222
[-0.05403629 -0.01456565  0.14911594  0.59505379]
Agent 60.22222222222222
[-0.0543276   0.17818935  0.16101702  0.35280765]
Agent 60.22222222222222
[-0.05076382 -0.01881214  0.16807317  0.6916222 ]
Agent 60.22222222222222
[-0.05114006  

[0.84728866 1.26636596 0.17176473 0.25927159]
Agent 42.0
[0.87261598 1.45867285 0.17695016 0.02530692]
Agent 42.0
[0.90178944 1.26151294 0.1774563  0.36818113]
Agent 42.0
[0.9270197  1.45372808 0.18481992 0.13628504]
Agent 42.0
[ 0.95609426  1.64578813  0.18754562 -0.09287044]
Agent 42.0
[0.98901002 1.44854241 0.18568822 0.25262577]
Agent 42.0
[1.01798087 1.64059462 0.19074073 0.02377884]
Agent 42.0
[ 1.05079277  1.83254223  0.19121631 -0.20318249]
Agent 42.0
[1.08744361 1.63527334 0.18715266 0.14320328]
Agent 42.0
[ 1.12014908  1.82729081  0.19001672 -0.08509117]
Agent 42.0
[1.15669489 1.63002512 0.1883149  0.26101086]
Agent 42.0
[1.18929539 1.82202984 0.19353512 0.03313335]
Agent 42.0
[ 1.22573599  2.01392582  0.19419778 -0.19279192]
Agent 42.0
[1.26601451 1.8166329  0.19034195 0.1543206 ]
Agent 42.0
[ 1.30234717  2.00859216  0.19342836 -0.07279476]
Agent 42.0
[ 1.34251901  2.2004909   0.19197246 -0.29876081]
Agent 42.0
[1.38652883 2.00322499 0.18599725 0.04779622]
Agent 42.0
[ 1.426

KeyboardInterrupt: 